In [ ]:
remotes::install_github("rstudio/reticulate")
remotes::install_github("rstudio/tensorflow")
remotes::install_github("rstudio/keras")
reticulate::miniconda_uninstall()
reticulate::install_miniconda()
keras::install_keras()

In [ ]:
library(reticulate)
reticulate::use_python("/usr/local/bin/python")
reticulate::use_condaenv("tensorflow")

In [ ]:
install.packages("tidyverse")

In [ ]:
#install.packages("reticulate")
#devtools::install_github("rstudio/reticulate") 
#devtools::install_github("rstudio/glue") 
#devtools::install_github("rstudio/jsonlite") 
#devtools::install_github("rstudio/lattice") 
#devtools::install_github("rstudio/magrittr") 
#devtools::install_github("rstudio/Matrix") 
#devtools::install_github("rstudio/png") 
#devtools::install_github("rstudio/processx") 
#devtools::install_github("rstudio/ps") 
#devtools::install_github("rstudio/R6") 
#devtools::install_github("rstudio/rappdirs") 
#devtools::install_github("rstudio/Rcpp") 
#devtools::install_github("rstudio/RcppTOML") 
#devtools::install_github("rstudio/rlang") 
#devtools::install_github("rstudio/rprojroot") 
#devtools::install_github("rstudio/tidyselect") 
#devtools::install_github("rstudio/vctrs") 
#devtools::install_github("rstudio/whisker") 
#devtools::install_github("rstudio/yaml") 
#devtools::install_github("rstudio/tensorflow") 
#install.packages('tensorflow')

In [1]:
#install.packages(c("keras","ramify"))
library(ramify)
library(cleanNLP)
#library(rJava)
library(plyr)
library(dplyr)
library(magrittr)
library(readxl)
library(stringr)
library(readr)
library(glue)
library(e1071)
library(forcats)
#library(tidyverse)
library(fastDummies)
#library(caret)
library(purrr)
#library(xgboost)
library(keras)
library(data.table)
library(tensorflow)


Attaching package: ‘ramify’

The following object is masked from ‘package:graphics’:

    clip


Attaching package: ‘dplyr’

The following objects are masked from ‘package:plyr’:

    arrange, count, desc, failwith, id, mutate, rename, summarise,
    summarize

The following objects are masked from ‘package:stats’:

    filter, lag

The following objects are masked from ‘package:base’:

    intersect, setdiff, setequal, union

Warning message:
“package ‘magrittr’ was built under R version 3.6.3”
Attaching package: ‘glue’

The following object is masked from ‘package:dplyr’:

    collapse

Warning message:
“package ‘fastDummies’ was built under R version 3.6.3”Warning message:
“package ‘purrr’ was built under R version 3.6.3”
Attaching package: ‘purrr’

The following object is masked from ‘package:magrittr’:

    set_names

The following object is masked from ‘package:plyr’:

    compact

The following object is masked from ‘package:ramify’:

    flatten


Attaching package: ‘data.tabl

In [3]:
use_boosting <- TRUE
# use_boosting <- FALSE
set.seed(2020)

# Change dimensions and cbind 47480,768

In [4]:
# load data
### df is the text features (tfidf?), but also the main thing that gets trained
### sample is actually the core data, with the text labels, but is only used at the end reporting accuracy etc
sample <- data.frame(fread("/Users/abhijit/IGRI Files/repo/step1_edit_data_sample.csv"))
embeddings <- data.frame(fread("/Users/abhijit/IGRI Files/repo/step1_edit_embedding_features.csv"))
df <- data.frame(fread("/Users/abhijit/IGRI Files/repo/step1_edit_data_df.csv")) ## EXTEND VOCABULARY
print(c("data size:", dim(df), dim(embeddings)))


[1] "data size:" "9494"       "29595"      "9494"       "3840"      


In [5]:
head(df)

ERROR while rich displaying an object: Error in sprintf(wrap, header, body): 'fmt' length exceeds maximal format length 8192

Traceback:
1. FUN(X[[i]], ...)
2. tryCatch(withCallingHandlers({
 .     if (!mime %in% names(repr::mime2repr)) 
 .         stop("No repr_* for mimetype ", mime, " in repr::mime2repr")
 .     rpr <- repr::mime2repr[[mime]](obj)
 .     if (is.null(rpr)) 
 .         return(NULL)
 .     prepare_content(is.raw(rpr), rpr)
 . }, error = error_handler), error = outer_handler)
3. tryCatchList(expr, classes, parentenv, handlers)
4. tryCatchOne(expr, names, parentenv, handlers[[1L]])
5. doTryCatch(return(expr), name, parentenv, handler)
6. withCallingHandlers({
 .     if (!mime %in% names(repr::mime2repr)) 
 .         stop("No repr_* for mimetype ", mime, " in repr::mime2repr")
 .     rpr <- repr::mime2repr[[mime]](obj)
 .     if (is.null(rpr)) 
 .         return(NULL)
 .     prepare_content(is.raw(rpr), rpr)
 . }, error = error_handler)
7. repr::mime2repr[[mime]](obj)
8. 

CodeType X.LSB. X. X.s a a. a.m. a.o abate ability ... zoology zu zubov
1 1        0      0  0   0 0  0    0   0     0       ... 0       0  0    
2 2        0      0  0   0 0  0    0   0     0       ... 0       0  0    
3 2        0      0  0   0 0  0    0   0     0       ... 0       0  0    
4 2        0      0  0   0 0  0    0   0     0       ... 0       0  0    
5 4        0      0  0   0 0  0    0   0     0       ... 0       0  0    
6 4        0      0  0   0 0  0    0   0     0       ... 0       0  0    
  zubova zubovski zueblin zum zweck zygoma zygomatic
1 0      0        0       0   0     0      0        
2 0      0        0       0   0     0      0        
3 0      0        0       0   0     0      0        
4 0      0        0       0   0     0      0        
5 0      0        0       0   0     0      0        
6 0      0        0       0   0     0      0

In [ ]:
colnames(df)[2450:2550]
colnames(sample)


In [33]:
df <- cbind(df, embeddings)

In [6]:
# as part of reading, convert back to factor
sample$sid_text <- NULL
sample$sid <- NULL
sample$tid <- NULL
sample[,1] <- factor( sample[,1] )
sample$CodeType <- factor( sample$CodeType )

In [7]:
# randomize order to make the following steps "random"
newOrder <- sample(1:nrow(df))
sample <- sample[newOrder,]
df <- df[newOrder,]

#final.training <- df[1:floor(0.9*nrow(df)),]
#final.test <- df[ceiling(0.9*nrow(df)):nrow(df),]

print(c(dim(final.training),dim(final.test)))

ERROR: Error in print(c(dim(final.training), dim(final.test))): object 'final.training' not found


# Test set cleaning and manipulation

In [66]:
vocab <- read.delim("full_vocab.txt", header = F)

In [67]:
vocab <- as.list(levels(vocab$V1))

In [71]:
(vocab)

[[1]]
[1] "-LSB-"

[[2]]
[1] "'"

[[3]]
[1] "'s"

[[4]]
[1] "a"

[[5]]
[1] "a."

[[6]]
[1] "a.m."

[[7]]
[1] "a.o"

[[8]]
[1] "aah"

[[9]]
[1] "aaron"

[[10]]
[1] "ab"

[[11]]
[1] "aback"

[[12]]
[1] "abacus"

[[13]]
[1] "abandon"

[[14]]
[1] "abandoned"

[[15]]
[1] "abandoning"

[[16]]
[1] "abandonment"

[[17]]
[1] "abandons"

[[18]]
[1] "abasement"

[[19]]
[1] "abashed"

[[20]]
[1] "abate"

[[21]]
[1] "abatement"

[[22]]
[1] "abbe"

[[23]]
[1] "abbey"

[[24]]
[1] "abbot"

[[25]]
[1] "abbots"

[[26]]
[1] "abbott"

[[27]]
[1] "abbreviations"

[[28]]
[1] "abc"

[[29]]
[1] "abdicate"

[[30]]
[1] "abdicated"

[[31]]
[1] "abdomen"

[[32]]
[1] "abdomens"

[[33]]
[1] "abdominal"

[[34]]
[1] "abduct"

[[35]]
[1] "abducted"

[[36]]
[1] "abducting"

[[37]]
[1] "abduction"

[[38]]
[1] "abductor"

[[39]]
[1] "abductors"

[[40]]
[1] "abe"

[[41]]
[1] "abel"

[[42]]
[1] "aberdeen"

[[43]]
[1] "abettors"

[[44]]
[1] "abeyance"

[[45]]
[1] "abhor"

[[46]]
[1] "abhorrence"

[[47]]
[1] "abhorrent"

[[48]]
[1] "abide"

[[49]]
[1] "abiding"

[[50]]
[1] "abigail"

[[51]]
[1] "abilities"

[[52]]
[1] "ability"

[[53]]
[1] "abject"

[[54]]
[1] "abjure"

[[55]]
[1] "ablaze"

[[56]]
[1] "able"

[[57]]
[1] "ablest"

[[58]]
[1] "ably"

[[59]]
[1] "abnegation"

[[60]]
[1] "abnormal"

[[61]]
[1] "abnormality"

[[62]]
[1] "abnormally"

[[63]]
[1] "aboard"

[[64]]
[1] "abode"

[[65]]
[1] "abodes"

[[66]]
[1] "abolish"

[[67]]
[1] "abolished"

[[68]]
[1] "abolishing"

[[69]]
[1] "abolition"

[[70]]
[1] "abolitionist"

[[71]]
[1] "abolitionists"

[[72]]
[1] "abominable"

[[73]]
[1] "abominably"

[[74]]
[1] "abomination"

[[75]]
[1] "abominations"

[[76]]
[1] "abort"

[[77]]
[1] "abortion"

[[78]]
[1] "abortive"

[[79]]
[1] "abound"

[[80]]
[1] "abounding"

[[81]]
[1] "about"

[[82]]
[1] "above"

[[83]]
[1] "aboveboard"

[[84]]
[1] "abraded"

[[85]]
[1] "abraham"

[[86]]
[1] "abramovna"

[[87]]
[1] "abrasion"

[[88]]
[1] "abrasions"

[[89]]
[1] "abreast"

[[90]]
[1] "abridge"

[[91]]
[1] "abridged"

[[92]]
[1] "abridging"

[[93]]
[1] "abroad"

[[94]]
[1] "abrogated"

[[95]]
[1] "abrupt"

[[96]]
[1] "abruptly"

[[97]]
[1] "abscess"

[[98]]
[1] "abscesses"

[[99]]
[1] "absence"

[[100]]
[1] "absences"

[[101]]
[1] "absent"

[[102]]
[1] "absentee"

[[103]]
[1] "absentees"

[[104]]
[1] "absently"

[[105]]
[1] "absentmindedly"

[[106]]
[1] "absolute"

[[107]]
[1] "absolutely"

[[108]]
[1] "absolutism"

[[109]]
[1] "absolved"

[[110]]
[1] "absorb"

[[111]]
[1] "absorbable"

[[112]]
[1] "absorbed"

[[113]]
[1] "absorbent"

[[114]]
[1] "absorbing"

[[115]]
[1] "absorption"

[[116]]
[1] "abstain"

[[117]]
[1] "abstained"

[[118]]
[1] "abstaining"

[[119]]
[1] "abstemious"

[[120]]
[1] "abstention"

[[121]]
[1] "abstiens"

[[122]]
[1] "abstract"

[[123]]
[1] "abstracted"

[[124]]
[1] "abstraction"

[[125]]
[1] "abstruse"

[[126]]
[1] "absurd"

[[127]]
[1] "absurdity"

[[128]]
[1] "absurdly"

[[129]]
[1] "abundance"

[[130]]
[1] "abundant"

[[131]]
[1] "abundantly"

[[132]]
[1] "abuse"

[[133]]
[1] "abused"

[[134]]
[1] "abuses"

[[135]]
[1] "abusing"

[[136]]
[1] "abusive"

[[137]]
[1] "abutted"

[[138]]
[1] "abyss"

[[139]]
[1] "ac"

[[140]]
[1] "acacia"

[[141]]
[1] "academic"

[[142]]
[1] "academies"

[[143]]
[1] "academy"

[[144]]
[1] "acadia"

[[145]]
[1] "acceded"

[[146]]
[1] "acceding"

[[147]]
[1] "accelerate"

[[148]]
[1] "accelerated"

[[149]]
[1] "accent"

[[150]]
[1] "accents"

[[151]]
[1] "accentuated"

[[152]]
[1] "accentuating"

[[153]]
[1] "accept"

[[154]]
[1] "acceptable"

[[155]]
[1] "acceptance"

[[156]]
[1] "accepted"

[[157]]
[1] "accepting"

[[158]]
[1] "accepts"

[[159]]
[1] "acces"

[[160]]
[1] "access"

[[161]]
[1] "accessed"

[[162]]
[1] "accessibility"

[[163]]
[1] "accessible"

[[164]]
[1] "accession"

[[165]]
[1] "accessory"

[[166]]
[1] "accident"

[[167]]
[1] "accidental"

[[168]]
[1] "accidentally"

[[169]]
[1] "accidently"

[[170]]
[1] "accidents"

[[171]]
[1] "acclaimed"

[[172]]
[1] "acclamation"

[[173]]
[1] "acclamations"

[[174]]


In [16]:
test <- read.csv("/Users/abhijit/IGRI Files/test.csv", header = TRUE)

In [20]:
test <- test[!grepl("[[:punct:]]", test$word), ]
test <- test[!grepl("[[:digit:]]", test$word), ]
test = test[test$tid != 0,]


In [89]:
test$word = droplevels(test$word)
testwords = as.list(levels(test$word))


In [87]:
test = test[test$word != '“',]
test = test[test$word != '”',]
test = test[test$word != 'backflow',]
test = test[test$word != 'certified',]
test = test[test$word != 'cpvc',]
test = test[test$word != 'installing',]
test = test[test$word != 'occupancies',]
test = test[test$word != 'preventers',]
test = test[test$word != 'reviewer',]
test = test[test$word != 'rme',]
test = test[test$word != 'sprinkler',]

In [90]:
length(setdiff(vocab,testwords))
length(setdiff(testwords,vocab))

[1] 29501

[1] 0

In [91]:
setdiff(testwords,vocab)

list()

In [92]:
vocab_ext = as.list(setdiff(vocab,testwords))

In [93]:
length(unique(vocab))
length(unique(testwords))
length((vocab_ext))

[1] 29595

[1] 94

[1] 29501

In [94]:
dumdum = dummy_cols(test,select_columns = "word", remove_selected_columns = TRUE)

In [101]:
dumdum = dumdum[,-c(1,2)]

In [95]:
matrix_ext =(setNames(data.frame(matrix(0, nrow = dim(test)[1], ncol = length(vocab_ext))),vocab_ext))

In [96]:
colnames(dumdum) = gsub(x = colnames(dumdum), pattern = "word_", replacement = "")  


In [104]:
final.test = cbind(dumdum, matrix_ext)
final.training = df

In [105]:
dim(final.training)
dim(final.test)

[1]  9494 29595

[1]   198 29595

In [106]:
X_train <- final.training %>% 
  select(-CodeType) %>%
  scale()


In [107]:
dim(final.training)

[1]  9494 29595

In [108]:
X_test <- final.test %>% 
#  select(-CodeType) %>%
  scale()

dim(X_test)

#X_test <- t(na.omit(t(X_test)))
dim(X_test)
dim(X_train)

[1]   198 29595

[1]   198 29595

[1]  9494 29594

In [39]:
y_train <- final.training$CodeType

In [40]:
y_test <- final.test$CodeType


In [13]:
dim(X_train)
dim(X_test)
length(y_test)

[1]  8544 33434

[1]   950 33434

[1] 950

In [43]:
X_train[is.na(X_train)] <- 0
X_test[is.na(X_test)] <- 0

In [44]:
head(X_train)
head(X_test)

X.LSB. X. X.s a          a.          a.m. a.o abate       ability     able
9452 0      0  0   -0.1208496 -0.01081856 0    0   -0.01081856 -0.01081856 0   
7767 0      0  0   -0.1208496 -0.01081856 0    0   -0.01081856 -0.01081856 0   
8920 0      0  0   -0.1208496 -0.01081856 0    0   -0.01081856 -0.01081856 0   
4417 0      0  0   -0.1208496 -0.01081856 0    0   -0.01081856 -0.01081856 0   
8465 0      0  0   -0.1208496 -0.01081856 0    0   -0.01081856 -0.01081856 0   
9380 0      0  0   -0.1208496 -0.01081856 0    0   -0.01081856 -0.01081856 0   
     ⋯ X3830       X3831       X3832      X3833      X3834        X3835     
9452 ⋯  1.14294576 -0.09416375 -0.7392135 -0.8669120  1.714268452 -0.4605348
7767 ⋯  0.07046407  0.76086230  0.9098201  0.3247471 -0.073480012 -0.4082870
8920 ⋯  0.46651151 -0.57876740 -0.4954576 -0.9392743 -0.892253598  1.2475406
4417 ⋯ -0.03717391  0.70597254 -0.3992676  0.4829841 -0.118411702  0.2994272
8465 ⋯  1.25592834 -0.71799018  0.2413195 -0.7220415 -0.007056762  0.4794235
9380 ⋯ -1.14130229  1.00098013 -0.2962240 -0.2454369 -1.046086199 -0.8966982
     X3836       X3837      X3838      X3839     
9452  0.75456612  1.0425514  0.6946639 -0.4719536
7767  0.06298599 -0.4506616  1.5855643 -0.7651742
8920 -0.38509368 -1.5691527 -1.0771948  0.3300504
4417 -0.68689222 -0.1379490  0.3234533 -1.0464238
8465  0.35269855 -0.3251331 -0.9280811 -0.6235524
9380  0.03589222 -0.1497445  0.2443217 -0.5458675

X.LSB. X. X.s a          a. a.m. a.o abate ability able ⋯ X3830       
1369 0      0  0   -0.1308151 0  0    0   0     0       0    ⋯  1.138680259
8320 0      0  0   -0.1308151 0  0    0   0     0       0    ⋯  1.576635918
6743 0      0  0   -0.1308151 0  0    0   0     0       0    ⋯  0.647668128
3063 0      0  0   -0.1308151 0  0    0   0     0       0    ⋯ -0.004313082
4049 0      0  0   -0.1308151 0  0    0   0     0       0    ⋯ -0.740948813
6471 0      0  0   -0.1308151 0  0    0   0     0       0    ⋯  0.308700610
     X3831      X3832       X3833      X3834      X3835       X3836      
1369 -1.2657484 -1.15499372 -0.4023195 -0.3889208  1.31748771 -0.41243228
8320 -1.2599857 -0.34897274 -0.3179876  0.7568089  0.01111533 -0.06739294
6743 -0.7812932 -0.05298048  1.1743218 -0.3700338  0.18610962 -0.78079979
3063  2.6830050 -0.75579086  1.4300901  0.7836917 -1.02327128 -0.48959329
4049  1.2990395  1.20053361  0.4353525  0.1855855 -0.30939013 -1.71060568
6471  0.4130982 -0.99874213  0.3712436  1.0526887 -0.18583532  0.23700624
     X3837      X3838       X3839      
1369 -0.1974426  0.06838984 -0.94481052
8320 -1.2625425  0.89302424 -0.90022846
6743 -0.1975956  1.10092361 -0.02855024
3063 -1.3828800 -0.02952727  1.22635096
4049 -1.2740936 -1.09762965  0.99962665
6471  1.1315456 -0.76676122 -1.14869426

In [ ]:
X_train <- final.training %>% 
  select(-CodeType) %>%
  scale()


X_train <- t(na.omit(t(X_train)))
#trainyboi <- t(is.na(t(X_train)))
y_train <- final.training$CodeType

X_test <- final.test %>% 
  select(-CodeType) %>%
  scale()

X_test <- t(na.omit(t(X_test)))
#testyboi <- t(is.na(t(X_test)))


common = (intersect(colnames(X_train), colnames(X_test)))
X_train <- X_train[ ,common]
X_test <- X_test[ ,common]

print(c(dim(X_train),dim(X_test)))


y_test <- final.test$CodeType


In [ ]:
getwd()
write.csv(trainyboi,"training na boiz.csv")
head(trainyboi)


In [45]:
#colnames(X_train)
#str(y_test)
print(dim(X_test))
print(c(dim(X_train),dim(X_test)))

[1]   950 33434
[1]  8544 33434   950 33434


In [ ]:
dim(X_train)
dim(y_train)
dim(X_test)
dim(y_test)

In [ ]:
length(y_train)

In [46]:
model <- keras_model_sequential() 



In [47]:
model %>% 
  layer_dense(units = 796, activation = 'relu', input_shape = ncol(X_train)) %>% 
  layer_dropout(rate = 0.1) %>%
  layer_dense(units = 1012, activation = 'relu') %>%
  layer_dropout(rate = 0.1) %>%
  layer_dense(units = 619, activation = 'relu') %>%
  layer_dropout(rate = 0.1) %>%
  layer_dense(units = 6, activation = 'softmax')

In [48]:
model %>% compile(
  loss = 'sparse_categorical_crossentropy',
  optimizer = 'adam',
  metrics = 'accuracy'
)


In [56]:
model %>% fit(
  X_train, y_train, 
  epochs = 100, 
  batch_size = 64,
  validation_split = 0.1,
  verbose = 1
)

In [ ]:
model %>% save_model_tf("modelz")

In [ ]:
getwd()

In [57]:
score <- model %>% evaluate(
  X_test, y_test,
  batch_size = 64
)

In [58]:
train_probs <- model %>% predict(
  X_train
)
test_probs <- model %>% predict(
  X_test
)

train_probs <- data.frame(train_probs)
test_probs <- data.frame(test_probs)

X_train_new <- cbind(X_train, train_probs)
X_test_new <- cbind(X_test, test_probs)


train_sample <- sample[1:floor(0.9*nrow(df)),]
test_sample <- sample[ceiling(0.9*nrow(df)):nrow(df),]
compare_data <- test_sample

In [59]:
y_pred_neural <- argmax(predict(model, X_test),rows=TRUE) - 1 #predict_classes(model, X_test)
compare_data$predicted_1st_round <- y_pred_neural
compare_data$predicted_1st_round_label <- mapvalues(compare_data$predicted_1st_round,
                                                    from = c(0,1,2,3,4,5),
                                                    to = c("Aim", "Attribute", "Condition", "Deontic", "Object", "Orelse"))

In [60]:
compare_data

word        CodeType  Code predicted_1st_round predicted_1st_round_label
1369 expenses    Condition 2    4                   Object                   
8320 annual      Condition 2    4                   Object                   
6743 council     Condition 2    1                   Attribute                
3063 will        Deontic   3    3                   Deontic                  
4049 selection   Object    4    2                   Condition                
6471 processors  Object    4    4                   Object                   
1100 with        Object    4    2                   Condition                
5345 the         Condition 2    2                   Condition                
5770 council     Object    4    4                   Object                   
740  of          Condition 2    2                   Condition                
8399 food        Object    4    4                   Object                   
4569 factors     Object    4    2                   Condition                
628  shall       Deontic   3    4                   Object                   
1003 in          Object    4    4                   Object                   
9382 portions    Condition 2    2                   Condition                
7910 the         Object    4    4                   Object                   
2392 one         Object    4    4                   Object                   
6113 may         Deontic   3    3                   Deontic                  
4758 the         Condition 2    2                   Condition                
4174 shall       Deontic   3    2                   Condition                
6678 supervision Condition 2    2                   Condition                
4464 and         Object    4    4                   Object                   
5378 across      Condition 2    2                   Condition                
1034 chair       Object    4    4                   Object                   
3293 represent   Aim       0    1                   Attribute                
1757 the         Object    4    4                   Object                   
1604 department  Object    4    4                   Object                   
5784 the         Object    4    2                   Condition                
8622 become      Condition 2    2                   Condition                
2277 advisory    Object    4    4                   Object                   
⋮    ⋮           ⋮         ⋮    ⋮                   ⋮                        
8388 information Object    4    4                   Object                   
2906 recommend   Aim       0    0                   Aim                      
7505 and         Object    4    2                   Condition                
1105 any         Object    4    4                   Object                   
2246 awareness   Condition 2    2                   Condition                
4514 be          Aim       0    0                   Aim                      
2613 more        Condition 2    2                   Condition                
4715 statistical Object    4    2                   Condition                
7340 council     Object    4    4                   Object                   
7769 council     Attribute 1    1                   Attribute                
6450 individual  Object    4    4                   Object                   
5004 appointed   Condition 2    1                   Attribute                
7433 every       Condition 2    2                   Condition                
181  council     Attribute 1    2                   Condition                
6046 methods     Object    4    4                   Object                   
2706 to          Condition 2    2                   Condition                
7401 the         Object    4    4                   Object                   
844  systems     Condition 2    2                   Condition                
4772 with        Condition 2    2                   Condition                
2417 from        Object    

In [61]:
myClasses <- as.matrix(table(compare_data$CodeType, compare_data$predicted_1st_round_label))
n <- sum(myClasses)
nc <- nrow(myClasses)
myDiag <- diag(myClasses)
myRowSums <- apply(myClasses, 1, sum)
myColSums <- apply(myClasses, 2, sum)
p <-  myRowSums / n
q <- myColSums / n

myAccuracy <- sum(myDiag) / n
precision <- myDiag / myColSums
recall <- myDiag / myRowSums
f1 <- (2 * precision * recall ) / (precision + recall)


In [62]:
short_data <- compare_data
colnames(short_data)[1] <- "word"
myStops <- c("the", "of", "a", "an", "and", "is", "it")
myDrops <- which(short_data$word %in% myStops)
short_data <- short_data[-myDrops,]

cat("Accuracy with neural network ", sum(compare_data$Code ==compare_data$predicted_1st_round)/nrow(compare_data)*100, "\n")
cat("Accuracy with neural network (w/out stop words)", sum(short_data$Code ==short_data$predicted_1st_round)/nrow(short_data)*100, "\n")
cat(" F1:", colnames(myClasses ), "\n")
cat(" F1:", f1, "\n")


pred_neural <- argmax(predict(model, X_test),rows=TRUE) - 1 #predict_classes(model, X_test)
#sample$Pred_Code <- pred_neural
#sample$Pred_CodeType <- mapvalues(sample$Pred_Code,from = c(0,1,2,3,4,5),to = c("Aim", "Attribute", "Condition", "Deontic", "Object", "Orelse"))

#print(head(sample,20))
#write.csv(sample_pred, "data/asf_sampled_predictions.csv", row.names=FALSE)


Accuracy with neural network  64.73684 
Accuracy with neural network (w/out stop words) 63.70757 
 F1: Aim Attribute Condition Deontic Object Orelse 
 F1: 0.275 0.2131148 0.6649007 0.6779661 0.7258248 0.4 


In [ ]:
(pred_neural)
(y_test)